In [276]:
from string import digits
import re
import pandas as pd
import nltk
from nltk.corpus import stopwords
from nltk import pos_tag, word_tokenize
from pymorphy2 import MorphAnalyzer
from wordcloud import WordCloud
from matplotlib import pyplot as plt


pd.set_option('display.max_rows', 500)
pd.set_option('display.max_columns', 500)
pd.set_option('display.max_colwidth', 5000)
nltk.download('stopwords')
nltk.download('punkt')
nltk.download('averaged_perceptron_tagger')
nltk.download('averaged_perceptron_tagger_ru')

[nltk_data] Downloading package stopwords to
[nltk_data]     D:\Users\mo1\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package punkt to
[nltk_data]     D:\Users\mo1\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     D:\Users\mo1\AppData\Roaming\nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!
[nltk_data] Downloading package averaged_perceptron_tagger_ru to
[nltk_data]     D:\Users\mo1\AppData\Roaming\nltk_data...
[nltk_data]   Package averaged_perceptron_tagger_ru is already up-to-
[nltk_data]       date!


True

In [277]:
tokenizer = nltk.RegexpTokenizer(r"\w+")
morph = MorphAnalyzer()
stopWordsALL = []
stopWordsRU = stopwords.words("russian")
stopWordsEN = stopwords.words("english")
stopWordsALL.extend(stopWordsEN)
stopWordsALL.extend(["который", "это", "каждый", "как", "почему", "на", "для", "наш", "можно", "можете", "другой", "мы", "разный", "более"])
punctuations = '''!#$%&'()*,./:;<=>?@\^_`{|}~«»—+₽™⠀"'''

def removeEmoji(text):
    regrex_pattern = re.compile(pattern = "["
        u"\U0001F600-\U0001F64F"  # emoticons
        u"\U0001F300-\U0001F5FF"  # symbols & pictographs
        u"\U0001F680-\U0001F6FF"  # transport & map symbols
        u"\U0001F1E0-\U0001F1FF"  # flags (iOS)
                           "]+", flags = re.UNICODE)
    return regrex_pattern.sub(r'',text)

def lemmatisation(text):
    """Очищает текст от "мусора" (пунктуация, эмодзм)
    Каждое слово ставится в свою первоначальную форму.
    Вернут список строк"""
    tokens = nltk.word_tokenize(removeEmoji(text.lower().translate(str.maketrans('', '', digits))))
    tokens = [morph.parse(token)[0].normal_form for token in tokens if token not in stopWordsALL\
              and token != " " \
              and token.strip() not in punctuations\
              and len(token) > 2]
    return tokens

In [278]:
data = pd.read_json("../data/summary_of_companies.json", orient='index')
companyNames = data.index
data = data.set_index([pd.Index([index for index in range(1, data.shape[0] + 1)])])
data.insert(0, 'Company', companyNames)

In [279]:
# конвентировать список строк в строку.
# None если пустой спикок (компания не казала какую-то конкретную информацию)
for id, company in enumerate(data['Industries'], start=1):
    data['Industries'][id] = ' '.join(data['Industries'][id]) if len(data['Industries'][id]) !=0 else 'None'
    data['Hubs'][id] = ' '.join(data['Hubs'][id]) if len(data['Hubs'][id]) !=0 else 'None'
    data['About'][id] = data['About'][id] if len(data['About'][id]) !=0 else 'None'
    data['Description'][id] = data['Description'][id] if len(data['Description'][id]) !=0 else 'None'
data

D:\Users\mo1\PycharmProjects\ML-Olimp\venv\lib\site-packages\ipykernel_launcher.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  after removing the cwd from sys.path.
D:\Users\mo1\PycharmProjects\ML-Olimp\venv\lib\site-packages\ipykernel_launcher.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """
D:\Users\mo1\PycharmProjects\ML-Olimp\venv\lib\site-packages\ipykernel_launcher.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  


Company  \
1                                            RUVDS.com   
2                                             Selectel   
3                                        Timeweb Cloud   
4                                                 OTUS   
5                                               Яндекс   
6                                    Open Data Science   
7                                                   VK   
8                                             ГК ЛАНИТ   
9                                             getmatch   
10                                            FirstVDS   
11                   Конференции Олега Бунина (Онтико)   
12                                               AGIMA   
13                                          Альфа-Банк   
14                               Postgres Professional   
15                                           Ozon Tech   
16                                         Southbridge   
17                                             TINKOFF   
18                                    Dodo Engineering   
19                           «Лаборатория Касперского»   
20                                        Хабр Карьера   
21                                   М.Видео-Эльдорадо   
22                                            CloudMTS   
23                                             Туту.ру   
24                                         Группа НЛМК   
25                                  ua-hosting.company   
26                                               YADRO   
27                            Издательский дом «Питер»   
28                                       Онлайн Патент   
29                                             Neoflex   
30                                           AvitoTech   
31                                                 МТС   
32                                    Ростелеком-Солар   
33                                              Skyeng   
34                                     Sportmaster Lab   
35                                               Флант   
36                                                 KTS   
37                                            Maxilect   
38                                         Газпромбанк   
39                                        Белая Радуга   
40                                             Бастион   
41                                         VAS Experts   
42                                              Контур   
43                                             Usetech   
44                                          GlobalSign   
45                                           Third Man   
46                                         Wiren Board   
47                                                ИТМО   
48                                                Сбер   
49                                                QIWI   
50                                                Хабр   
51                                    Яндекс Практикум   
52                                             МойОфис   
53                                             EvaTeam   
54                                              Тензор   
55                                         SberDevices   
56                         РСХБ-Интех (Россельхозбанк)   
57                                    Home Credit Bank   
58                                       red_mad_robot   
59                                    Инфосистемы Джет   
60                                           Группа Т1   
61                                          PVS-Studio   
62                               Группа компаний X-Com   
63                                                КРОК   
64                                 Productivity Inside   
65                                                 ВТБ   
66                                                2ГИС   
67                                               АСКОН   
68                                        Журнал Хакер   
69                                          R

In [280]:
# применить лемматизацию
data['Industries'] = data['Industries'].apply(lemmatisation)
data['Hubs'] = data['Hubs'].apply(lemmatisation)
data['Description'] = data['Description'].apply(lemmatisation)
data['About'] = data['About'].apply(lemmatisation)
data

Company  \
1                                            RUVDS.com   
2                                             Selectel   
3                                        Timeweb Cloud   
4                                                 OTUS   
5                                               Яндекс   
6                                    Open Data Science   
7                                                   VK   
8                                             ГК ЛАНИТ   
9                                             getmatch   
10                                            FirstVDS   
11                   Конференции Олега Бунина (Онтико)   
12                                               AGIMA   
13                                          Альфа-Банк   
14                               Postgres Professional   
15                                           Ozon Tech   
16                                         Southbridge   
17                                             TINKOFF   
18                                    Dodo Engineering   
19                           «Лаборатория Касперского»   
20                                        Хабр Карьера   
21                                   М.Видео-Эльдорадо   
22                                            CloudMTS   
23                                             Туту.ру   
24                                         Группа НЛМК   
25                                  ua-hosting.company   
26                                               YADRO   
27                            Издательский дом «Питер»   
28                                       Онлайн Патент   
29                                             Neoflex   
30                                           AvitoTech   
31                                                 МТС   
32                                    Ростелеком-Солар   
33                                              Skyeng   
34                                     Sportmaster Lab   
35                                               Флант   
36                                                 KTS   
37                                            Maxilect   
38                                         Газпромбанк   
39                                        Белая Радуга   
40                                             Бастион   
41                                         VAS Experts   
42                                              Контур   
43                                             Usetech   
44                                          GlobalSign   
45                                           Third Man   
46                                         Wiren Board   
47                                                ИТМО   
48                                                Сбер   
49                                                QIWI   
50                                                Хабр   
51                                    Яндекс Практикум   
52                                             МойОфис   
53                                             EvaTeam   
54                                              Тензор   
55                                         SberDevices   
56                         РСХБ-Интех (Россельхозбанк)   
57                                    Home Credit Bank   
58                                       red_mad_robot   
59                                    Инфосистемы Джет   
60                                           Группа Т1   
61                                          PVS-Studio   
62                               Группа компаний X-Com   
63                                                КРОК   
64                                 Productivity Inside   
65                                                 ВТБ   
66                                                2ГИС   
67                                               АСКОН   
68                                        Журнал Хакер   
69                                          R

In [281]:
def getWordsFromListOfTaggedWords(taggedWords):
    """Отобрать слова от тегов"""
    return [taggedWord[0] for taggedWord in taggedWords]

def getOnlyNeedTags(text):
    """Отобрать только нужные теги"""
    TAGS = ['NONLEX', 'A=m', 'S']
    words = []
    text = word_tokenize(" ".join(text))
    for word, tag in pos_tag(text, lang='rus'):
        if tag in TAGS:
            words.append((word, tag))
    return words

def buildWordCloudComparisonChart(companyName, text, save=False):
    """Построить график "облако слов"
    Облака слов или, как мы привыкли, word clouds — это изображения, которые формируются из списка слов. Обычно, чем чаще слово появляется в списке, тем большего размера или чаще оно будет встречаться в облаке слов. Word cloud необязательно имеет форму облака."""
    companyName = companyName.translate(str.maketrans('', '', punctuations))
    textString = " ".join(text)
    wordCloudBeforeTagging = WordCloud(stopwords=stopWordsALL, width=800, height=800).generate(textString)
    textTaggedString = " ".join(getWordsFromListOfTaggedWords(getOnlyNeedTags(text)))
    wordCloudAfterTagging = WordCloud(stopwords=stopWordsALL, width=800, height=800).generate(textTaggedString)
    fig, (ax1, ax2) = plt.subplots(1, 2, layout='constrained', sharey=True, figsize=(16, 9))
    ax1.imshow(wordCloudBeforeTagging)
    ax2.imshow(wordCloudAfterTagging)
    ax1.axis("off")
    ax2.axis("off")
    fig.suptitle("Отбор тегов", fontsize=20)
    ax1.set_title("До отбора тегов", fontsize=16)
    ax2.set_title("После отбора тегов", fontsize=16)
    if save:
        fig.savefig(f"data/WordClouds/{companyName}.png")
    else:
        plt.show()
    plt.close(fig)

In [282]:
# графики находятся в data/WordClouds
# Ячейка не выполнена, т.к. графики уже созданы. Нет смысла повторять дорогостоящую операцию.
# for companyID in range(1, len(data) + 1):
#     buildWordCloudComparisonChart(data["Company"][companyID], data["About"][companyID], save=True)

# Modele Б

In [283]:
data["fullData"] = None

In [284]:
for id, company in enumerate(data['Industries'], start=1):
    data["fullData"][id] = " ".join(getWordsFromListOfTaggedWords(getOnlyNeedTags(data["Description"][id]))) + " " + " ".join(getWordsFromListOfTaggedWords(getOnlyNeedTags(data["Industries"][id]))) + " "  + " ".join(getWordsFromListOfTaggedWords(getOnlyNeedTags(data["Hubs"][id]))) + " "  + " ".join(getWordsFromListOfTaggedWords(getOnlyNeedTags(data["About"][id])))
data

D:\Users\mo1\PycharmProjects\ML-Olimp\venv\lib\site-packages\ipykernel_launcher.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  


Company  \
1                                            RUVDS.com   
2                                             Selectel   
3                                        Timeweb Cloud   
4                                                 OTUS   
5                                               Яндекс   
6                                    Open Data Science   
7                                                   VK   
8                                             ГК ЛАНИТ   
9                                             getmatch   
10                                            FirstVDS   
11                   Конференции Олега Бунина (Онтико)   
12                                               AGIMA   
13                                          Альфа-Банк   
14                               Postgres Professional   
15                                           Ozon Tech   
16                                         Southbridge   
17                                             TINKOFF   
18                                    Dodo Engineering   
19                           «Лаборатория Касперского»   
20                                        Хабр Карьера   
21                                   М.Видео-Эльдорадо   
22                                            CloudMTS   
23                                             Туту.ру   
24                                         Группа НЛМК   
25                                  ua-hosting.company   
26                                               YADRO   
27                            Издательский дом «Питер»   
28                                       Онлайн Патент   
29                                             Neoflex   
30                                           AvitoTech   
31                                                 МТС   
32                                    Ростелеком-Солар   
33                                              Skyeng   
34                                     Sportmaster Lab   
35                                               Флант   
36                                                 KTS   
37                                            Maxilect   
38                                         Газпромбанк   
39                                        Белая Радуга   
40                                             Бастион   
41                                         VAS Experts   
42                                              Контур   
43                                             Usetech   
44                                          GlobalSign   
45                                           Third Man   
46                                         Wiren Board   
47                                                ИТМО   
48                                                Сбер   
49                                                QIWI   
50                                                Хабр   
51                                    Яндекс Практикум   
52                                             МойОфис   
53                                             EvaTeam   
54                                              Тензор   
55                                         SberDevices   
56                         РСХБ-Интех (Россельхозбанк)   
57                                    Home Credit Bank   
58                                       red_mad_robot   
59                                    Инфосистемы Джет   
60                                           Группа Т1   
61                                          PVS-Studio   
62                               Группа компаний X-Com   
63                                                КРОК   
64                                 Productivity Inside   
65                                                 ВТБ   
66                                                2ГИС   
67                                               АСКОН   
68                                        Журнал Хакер   
69                                          R

In [285]:
from sklearn.feature_extraction.text import TfidfVectorizer
vectorizer = TfidfVectorizer()
got_tfidf = vectorizer.fit_transform(data["fullData"][87].split())
tfidf = pd.DataFrame(got_tfidf.toarray())
tfidf.columns = vectorizer.get_feature_names()
tfidf

D:\Users\mo1\PycharmProjects\ML-Olimp\venv\lib\site-packages\sklearn\utils\deprecation.py:87: FutureWarning: Function get_feature_names is deprecated; get_feature_names is deprecated in 1.0 and will be removed in 1.2. Please use get_feature_names_out instead.
  warnings.warn(msg, category=FutureWarning)


none  динамический  консалтинг  маркетинг  персонал  поддержка  продукт  \
0    0.0           0.0         0.0        0.0       0.0        0.0      0.0   
1    0.0           1.0         0.0        0.0       0.0        0.0      0.0   
2    0.0           0.0         0.0        0.0       0.0        0.0      0.0   
3    0.0           0.0         0.0        0.0       0.0        0.0      0.0   
4    0.0           0.0         0.0        1.0       0.0        0.0      0.0   
5    0.0           0.0         1.0        0.0       0.0        0.0      0.0   
6    0.0           0.0         0.0        0.0       0.0        1.0      0.0   
7    0.0           0.0         0.0        0.0       0.0        0.0      0.0   
8    0.0           0.0         0.0        0.0       0.0        0.0      0.0   
9    0.0           0.0         0.0        0.0       0.0        0.0      0.0   
10   0.0           0.0         0.0        0.0       0.0        0.0      1.0   
11   0.0           0.0         0.0        0.0       0.0        0.0      0.0   
12   0.0           0.0         0.0        0.0       1.0        0.0      0.0   
13   1.0           0.0         0.0        0.0       0.0        0.0      0.0   

    проект  разработка  реклама  стратегия  управление  
0      0.0         1.0      0.0        0.0         0.0  
1      0.0         0.0      0.0        0.0         0.0  
2      0.0         0.0      0.0        1.0         0.0  
3      0.0         0.0      1.0        0.0         0.0  
4      0.0         0.0      0.0        0.0         0.0  
5      0.0         0.0      0.0        0.0         0.0  
6      0.0         0.0      0.0        0.0         0.0  
7      0.0         0.0      0.0        0.0         1.0  
8      1.0         0.0      0.0        0.0         0.0  
9      0.0         0.0      0.0        0.0         1.0  
10     0.0         0.0      0.0        0.0         0.0  
11     0.0         0.0      0.0        0.0         1.0  
12     0.0         0.0      0.0        0.0         0.0  
13     0.0         0.0      0.0        0.0         0.0

In [286]:
import collections
from collections import Counter
data["bigrm"] = None
data["trigrams"] = None
data["keywords"] = None
for id, company in enumerate(data['Industries'], start=1):
    data["bigrm"][id] = list(nltk.bigrams(data["fullData"][id].split()))
    counter = collections.Counter(data["fullData"][id].split())
    most_common = counter.most_common()[0]
    data["keywords"][id] = most_common
data

D:\Users\mo1\PycharmProjects\ML-Olimp\venv\lib\site-packages\ipykernel_launcher.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  import sys
D:\Users\mo1\PycharmProjects\ML-Olimp\venv\lib\site-packages\ipykernel_launcher.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  # Remove the CWD from sys.path while we load stuff.


Company  \
1                                            RUVDS.com   
2                                             Selectel   
3                                        Timeweb Cloud   
4                                                 OTUS   
5                                               Яндекс   
6                                    Open Data Science   
7                                                   VK   
8                                             ГК ЛАНИТ   
9                                             getmatch   
10                                            FirstVDS   
11                   Конференции Олега Бунина (Онтико)   
12                                               AGIMA   
13                                          Альфа-Банк   
14                               Postgres Professional   
15                                           Ozon Tech   
16                                         Southbridge   
17                                             TINKOFF   
18                                    Dodo Engineering   
19                           «Лаборатория Касперского»   
20                                        Хабр Карьера   
21                                   М.Видео-Эльдорадо   
22                                            CloudMTS   
23                                             Туту.ру   
24                                         Группа НЛМК   
25                                  ua-hosting.company   
26                                               YADRO   
27                            Издательский дом «Питер»   
28                                       Онлайн Патент   
29                                             Neoflex   
30                                           AvitoTech   
31                                                 МТС   
32                                    Ростелеком-Солар   
33                                              Skyeng   
34                                     Sportmaster Lab   
35                                               Флант   
36                                                 KTS   
37                                            Maxilect   
38                                         Газпромбанк   
39                                        Белая Радуга   
40                                             Бастион   
41                                         VAS Experts   
42                                              Контур   
43                                             Usetech   
44                                          GlobalSign   
45                                           Third Man   
46                                         Wiren Board   
47                                                ИТМО   
48                                                Сбер   
49                                                QIWI   
50                                                Хабр   
51                                    Яндекс Практикум   
52                                             МойОфис   
53                                             EvaTeam   
54                                              Тензор   
55                                         SberDevices   
56                         РСХБ-Интех (Россельхозбанк)   
57                                    Home Credit Bank   
58                                       red_mad_robot   
59                                    Инфосистемы Джет   
60                                           Группа Т1   
61                                          PVS-Studio   
62                               Группа компаний X-Com   
63                                                КРОК   
64                                 Productivity Inside   
65                                                 ВТБ   
66                                                2ГИС   
67                                               АСКОН   
68                                        Журнал Хакер   
69                                          R

In [287]:
fullData = []
for id in range(1, len(data) + 1):
    fullData.extend([data["fullData"][id]])

Modele B

In [288]:
from collections import Counter

def match(text):
    alphabet = set('абвгдеёжзийклмнопрстуфхцчшщъыьэюя')
    return not alphabet.isdisjoint(text.lower())


def get_name_from_srp_blob(clean_blob):
    # blob = " ".join(clean_blob)
    # blob_tokens = list(filter(bool, map(lambda x: x if len(x) > 2 else '', blob.split(' '))))
    c = Counter(clean_blob)
    most_common = c.most_common(10)
    try:
        if match(f"{most_common[0][0]}"):
            return f"{most_common[0][0]}"
        else:
            return f"{most_common[1][0]}"
    except:
        return None


pipeline = lambda x: get_name_from_srp_blob(x)

In [289]:
from sklearn import preprocessing
encoder = preprocessing.LabelEncoder()


data["label"] = None
for id in range(1, len(data) + 1):
    data["label"][id] = pipeline(data["About"][id])

data['label'] = encoder.fit_transform(data['label'])
labels = data['label'].to_numpy()
data.to_csv("data/data.csv", index=False)


D:\Users\mo1\PycharmProjects\ML-Olimp\venv\lib\site-packages\ipykernel_launcher.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  import sys


In [290]:
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.model_selection import train_test_split
from sklearn.feature_extraction.text import TfidfTransformer


vectorizer = CountVectorizer(stop_words=stopWordsALL)
X = vectorizer.fit_transform(fullData).toarray()

tfidfconverter = TfidfTransformer()
X = tfidfconverter.fit_transform(X).toarray()
y = labels
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

In [291]:
from sklearn.linear_model import LinearRegression
from sklearn.metrics import mean_squared_error, r2_score

lr = LinearRegression()
lr.fit(X_train, y_train)
y_lr_train_pred = lr.predict(X_train)
y_lr_test_pred = lr.predict(X_test)

lr_train_mse = mean_squared_error(y_train, y_lr_train_pred)
lr_train_r2 = r2_score(y_train, y_lr_train_pred)
lr_test_mse = mean_squared_error(y_test, y_lr_test_pred)
lr_test_r2 = r2_score(y_test, y_lr_test_pred)
lr_score = lr.score(X_test, y_test)

lr_results = pd.DataFrame(['Linear regression',lr_train_mse, lr_train_r2, lr_test_mse, lr_test_r2, lr_score]).transpose()
lr_results.columns = ['Method','Training MSE','Training R2','Test MSE','Test R2', "Score"]
lr_results

Method Training MSE Training R2 Test MSE  Test R2    Score
0  Linear regression  1.75062e-26           1   2134.3  0.11957  0.11957

In [292]:
from sklearn.linear_model import LogisticRegression

logRL = LogisticRegression(solver='liblinear', multi_class='ovr')
logRL.fit(X_train, y_train)
y_logRL_train_pred = logRL.predict(X_train)
y_logRL_test_pred = logRL.predict(X_test)

logRL_train_mse = mean_squared_error(y_train, y_logRL_train_pred)
logRL_train_r2 = r2_score(y_train, y_logRL_train_pred)
logRL_test_mse = mean_squared_error(y_test, y_logRL_test_pred)
logRL_test_r2 = r2_score(y_test, y_logRL_test_pred)
logRL_score = lr.score(X_test, y_test)

logRL_results = pd.DataFrame(['LogisticRegression',logRL_train_mse, logRL_train_r2, logRL_test_mse, logRL_test_r2, logRL_score]).transpose()
logRL_results.columns = ['Method','Training MSE','Training R2','Test MSE','Test R2', "Score"]
logRL_results

Method Training MSE Training R2 Test MSE    Test R2    Score
0  LogisticRegression      3287.54   -0.170404  2644.28 -0.0908049  0.11957

In [293]:
from sklearn.tree import DecisionTreeClassifier

dfc = DecisionTreeClassifier()
dfc.fit(X_train, y_train)
y_dfc_train_pred = dfc.predict(X_train)
y_dfc_test_pred = dfc.predict(X_test)

dfc_train_mse = mean_squared_error(y_train, y_dfc_train_pred)
dfc_train_r2 = r2_score(y_train, y_dfc_train_pred)
dfc_test_mse = mean_squared_error(y_test, y_dfc_test_pred)
dfc_test_r2 = r2_score(y_test, y_dfc_test_pred)
dfc_score = lr.score(X_test, y_test)

dfc_results = pd.DataFrame(['DecisionTreeClassifier',dfc_train_mse, dfc_train_r2, dfc_test_mse, dfc_test_r2, dfc_score]).transpose()
dfc_results.columns = ['Method','Training MSE','Training R2','Test MSE','Test R2', "Score"]
dfc_results

Method Training MSE Training R2 Test MSE   Test R2    Score
0  DecisionTreeClassifier            0           1  3381.48 -0.394912  0.11957

In [294]:
from sklearn.ensemble import RandomForestRegressor
from sklearn.metrics import classification_report, confusion_matrix, accuracy_score

rf = RandomForestRegressor(max_depth=2, random_state=42)
rf.fit(X_train, y_train)
y_rf_train_pred = rf.predict(X_train)
y_rf_test_pred = rf.predict(X_test)

rf_train_mse = mean_squared_error(y_train, y_rf_train_pred)
rf_train_r2 = r2_score(y_train, y_rf_train_pred)
rf_test_mse = mean_squared_error(y_test, y_rf_test_pred)
rf_test_r2 = r2_score(y_test, y_rf_test_pred)
rf_score = rf.score(X_test, y_test)

rf_results = pd.DataFrame(['Random forest',rf_train_mse, rf_train_r2, rf_test_mse, rf_test_r2, rf_score]).transpose()
rf_results.columns = ['Method','Training MSE','Training R2','Test MSE','Test R2', "Score"]
rf_results

Method Training MSE Training R2 Test MSE   Test R2     Score
0  Random forest      2244.07    0.201083   2079.5  0.142175  0.142175

In [295]:
from sklearn.neighbors import KNeighborsClassifier

kn = KNeighborsClassifier()
kn.fit(X_train, y_train)
y_kn_train_pred = kn.predict(X_train)
y_kn_test_pred = kn.predict(X_test)

kn_train_mse = mean_squared_error(y_train, y_kn_train_pred)
kn_train_r2 = r2_score(y_train, y_kn_train_pred)
kn_test_mse = mean_squared_error(y_test, y_kn_test_pred)
kn_test_r2 = r2_score(y_test, y_kn_test_pred)
kn_score = kn.score(X_test, y_test)

kn_results = pd.DataFrame(['K-means', kn_train_mse, kn_train_r2, kn_test_mse, kn_test_r2, kn_score]).transpose()
kn_results.columns = ['Method','Training MSE','Training R2','Test MSE','Test R2', "Score"]
kn_results

Method Training MSE Training R2 Test MSE  Test R2    Score
0  K-means       4726.2   -0.682588   5490.5 -1.26491  0.09375

In [296]:
from sklearn.naive_bayes import GaussianNB

gs = GaussianNB()
gs.fit(X_train, y_train)
y_gs_train_pred = gs.predict(X_train)
y_gs_test_pred = gs.predict(X_test)

gs_train_mse = mean_squared_error(y_train, y_gs_train_pred)
gs_train_r2 = r2_score(y_train, y_gs_train_pred)
gs_test_mse = mean_squared_error(y_test, y_gs_test_pred)
gs_test_r2 = r2_score(y_test, y_gs_test_pred)
gs_score = kn.score(X_test, y_test)

gs_results = pd.DataFrame(['GaussianNB', gs_train_mse, gs_train_r2, gs_test_mse, gs_test_r2, gs_score]).transpose()
gs_results.columns = ['Method','Training MSE','Training R2','Test MSE','Test R2', "Score"]
gs_results

Method Training MSE Training R2 Test MSE   Test R2    Score
0  GaussianNB            0           1  3113.59 -0.284403  0.09375

In [297]:
from sklearn.svm import SVC

svc = SVC(gamma='auto')
svc.fit(X_train, y_train)
y_svc_train_pred = svc.predict(X_train)
y_svc_test_pred = svc.predict(X_test)

svc_train_mse = mean_squared_error(y_train, y_svc_train_pred)
svc_train_r2 = r2_score(y_train, y_svc_train_pred)
svc_test_mse = mean_squared_error(y_test, y_svc_test_pred)
svc_test_r2 = r2_score(y_test, y_svc_test_pred)
svc_score = kn.score(X_test, y_test)

svc_results = pd.DataFrame(['SVC', svc_train_mse, svc_train_r2, svc_test_mse, svc_test_r2, svc_score]).transpose()
svc_results.columns = ['Method','Training MSE','Training R2','Test MSE','Test R2', "Score"]
svc_results

Method Training MSE Training R2 Test MSE   Test R2    Score
0    SVC      4081.93   -0.453218  3353.45 -0.383349  0.09375

In [ ]:
import pickle

## Высшая точность у RandomForestRegressor

In [303]:
from sklearn.preprocessing import StandardScaler


def vector(text):

    vectorizer = CountVectorizer(stop_words=stopWordsALL)
    x = vectorizer.fit_transform(text[0].split()).toarray()

    scaler = StandardScaler()
    # fit and transform the data
    scaled_data = scaler.fit_transform(x)

    tfidfconverter = TfidfTransformer()
    return tfidfconverter.fit_transform(scaled_data).toarray()


to_predict = data[data['Company'] == 'RUVDS.com']
text = to_predict["fullData"].tolist()

rf.predict(X_test[0:320])



array([ 96.29370499,  97.40904071,  97.23909765,  97.70330174,
        97.30183063,  95.41954079,  95.37866333,  95.59595254,
       104.08070923, 101.01023521,  98.07454812,  98.0816931 ,
        98.6201663 ,  94.34289727,  94.92317783, 100.45214026,
        97.92508558,  98.10661488,  97.8371458 ,  98.48794201,
       100.22827503,  92.25723055,  96.89148078,  97.92508558,
        94.49041175,  95.58207431,  97.89602692,  97.98643254,
        97.76438731,  99.43893099, 100.08942703, 136.85226619,
        92.17027334,  96.79322651, 166.79135789,  91.34805786,
        98.72709483,  99.14231919,  96.50618467,  98.05993624,
        95.24612237, 101.69024313,  91.44420133,  97.55715845,
        95.24939214,  97.30708267,  98.64563912,  96.21637083,
       100.25989476,  97.22925641,  95.09479869,  97.87235157,
        98.54289726,  96.89148078,  87.66185601,  98.58596398,
       101.02961663,  95.88326539,  96.56427476,  97.82071291,
        95.92970115,  97.02357434, 168.13252297,  98.69